In [ ]:
# pip install colorcet

In [ ]:
import folium
import matplotlib
import numpy as np
import colorcet
from matplotlib.pyplot import imread
from matplotlib.colors import Normalize
from matplotlib.colors import ListedColormap
from folium import raster_layers
from folium import plugins
from folium import branca

In [ ]:
image = '/notebooks/resources/gpm/gpm_1d.20190531.tif'

In [ ]:
from osgeo import gdal,ogr,osr

def GetExtent(gt,cols,rows):
    ''' Return list of corner coordinates from a geotransform

        @type gt:   C{tuple/list}
        @param gt: geotransform
        @type cols:   C{int}
        @param cols: number of columns in the dataset
        @type rows:   C{int}
        @param rows: number of rows in the dataset
        @rtype:    C{[float,...,float]}
        @return:   coordinates of each corner
    '''
    ext=[]
    xarr=[0,cols]
    yarr=[0,rows]

    for px in xarr:
        for py in yarr:
            x=gt[0]+(px*gt[1])+(py*gt[2])
            y=gt[3]+(px*gt[4])+(py*gt[5])
            ext.append([y,x])
            print (y,x)
        yarr.reverse()
    return ext

def ReprojectCoords(coords,src_srs,tgt_srs):
    ''' Reproject a list of x,y coordinates.

        @type geom:     C{tuple/list}
        @param geom:    List of [[x,y],...[x,y]] coordinates
        @type src_srs:  C{osr.SpatialReference}
        @param src_srs: OSR SpatialReference object
        @type tgt_srs:  C{osr.SpatialReference}
        @param tgt_srs: OSR SpatialReference object
        @rtype:         C{tuple/list}
        @return:        List of transformed [[x,y],...[x,y]] coordinates
    '''
    trans_coords=[]
    transform = osr.CoordinateTransformation( src_srs, tgt_srs)
    for x,y in coords:
        x,y,z = transform.TransformPoint(x,y)
        trans_coords.append([x,y])
    return trans_coords

raster=image
ds=gdal.Open(raster)

gt=ds.GetGeoTransform()
cols = ds.RasterXSize
rows = ds.RasterYSize

ext=GetExtent(gt,cols,rows)
print("ext = " + str(ext))

src_srs=osr.SpatialReference()
src_srs.ImportFromWkt(ds.GetProjection())
# tgt_srs=osr.SpatialReference()
# tgt_srs.ImportFromEPSG(3857)
tgt_srs = src_srs.CloneGeogCS()

geo_ext=ReprojectCoords(ext,src_srs,tgt_srs)
print("geo_ext = " + str(geo_ext))

In [ ]:
!gdalinfo '/notebooks/resources/gpm/gpm_1d.20190531.tif'

In [ ]:
# !gdal_edit -colorinterp_1 alpha /notebooks/resources/gpm/gpm_1d.20190531.tif

In [ ]:
# Choose colormap
cmap = colorcet.cm.fire

# Get the colormap colors
my_cmap = cmap(np.arange(cmap.N))


# Set alpha
my_cmap[:,-1] = np.linspace(0, 1, cmap.N)

# Create new colormap
my_cmap = ListedColormap(my_cmap)



In [ ]:
m = folium.Map(
      location = [-22, -114]
    , zoom_start = 2
    , control_scale = True 
    , tiles = 'Stamen Terrain'
)

data = matplotlib.pyplot.imread(image)

# Image bounds on the map in the form
# [[lat_min, lon_min], [lat_max, lon_max]]
m.add_child(raster_layers.ImageOverlay(
      data
    , opacity = 0.7
    , bounds = [ext[2], ext[0]]
    , mercator_project = True
#     , colormap = lambda x: (1, 0, 0, x)
    , colormap = colorcet.cm.fire
#     , colormap = branca.colormap.linear.PuBuGn_07.scale(0,700)
#     , colormap = my_cmap
)
           )

folium.Marker(
      ext[2]
    , popup = str(ext[2])
    , tooltip = str(ext[2])
).add_to(m)

folium.Marker(
      ext[0]
    , popup = str(ext[0])
    , tooltip = str(ext[0])
).add_to(m)

m

In [ ]:
vars(m)

In [ ]:
print(data)
print(data.shape)
# data = data.transpose()
# print(data)
# print(data.shape)

In [ ]:
# First: read the geotiff image with GDAL.
from osgeo import gdal, osr

gdal.UseExceptions()

ds = gdal.Open(image)
data = ds.ReadAsArray()
gt = ds.GetGeoTransform()
proj = ds.GetProjection()

inproj = osr.SpatialReference()
inproj.ImportFromWkt(proj)

print('\n\n## ds ##:\n\n' + str(ds))
print('\n\n## data ##:\n\n' + str(data))
print('\n\n## gt ##:\n\n' + str(gt))
print('\n\n## proj ##:\n\n' + str(proj))
print('\n\n## inproj ##:\n\n' + str(inproj))

In [ ]:
q = lambda x: (0, 0, 0, 0)
print(q(0))

In [ ]:
cmap = colorcet.cm.bmw

rgba = cmap(0.5)
print(rgba) # (0.99807766255210428, 0.99923106502084169, 0.74602077638401709, 1.0
print(rgba[:-1])



In [ ]:
import numpy as np
import matplotlib.pylab as pl
from matplotlib.colors import ListedColormap

# Random data
data1 = np.random.random((4,4))

# Choose colormap
cmap = pl.cm.RdBu

# Get the colormap colors
my_cmap = cmap(np.arange(cmap.N))

# Set alpha
my_cmap[:,-1] = np.linspace(0, 1, cmap.N)

# Create new colormap
my_cmap = ListedColormap(my_cmap)

pl.figure()
pl.subplot(121)
pl.pcolormesh(data1, cmap=pl.cm.RdBu)
pl.colorbar()

pl.subplot(122)
pl.pcolormesh(data1, cmap=my_cmap)
pl.colorbar()

In [ ]:
# Choose colormap
cmap = colorcet.cm.fire

# Get the colormap colors
my_cmap = cmap(np.arange(cmap.N))

print(my_cmap)

# Set alpha
my_cmap[:,-1] = np.linspace(0, 1, cmap.N)

# Create new colormap
my_cmap = ListedColormap(my_cmap)

pl.figure()
pl.subplot(121)
pl.pcolormesh(data1, cmap=colorcet.cm.fire)
pl.colorbar()

pl.subplot(122)
pl.pcolormesh(data1, cmap=my_cmap)
pl.colorbar()

In [22]:
import branca
# branca.colormap.linear.Spectral_04
colormap = branca.colormap.linear.Spectral_04.scale(0, 10000)
colormap = colormap.to_step(index=[0, 25, 50, 100, 250, 500, 1000, 2500, 5000, 10000])
colormap.caption = 'mm'
colormap

In [39]:
import branca


colormap = branca.colormap.StepColormap(
    ['#64abb0','#9dd3a7', '#c7e9ad', '#edf8b9', '#ffedaa', '#fec980', '#f99e59', '#e85b3a', '#d7191c'],
    vmin=0, vmax=10000,
    index=[0, 25, 50, 100, 250, 500, 1000, 2500, 5000, 10000],
    caption='step'
)

colormap

In [32]:
cm.StepColormap(['#64abb0'])

In [ ]:
ftp://jsimpson.pps.eosdis.nasa.gov/NRTPUB/imerg/gis/README.GIS.pdf